In [ ]:
!pip install geojsoncontour

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import pandas as pd
import numpy as np
from datetime import datetime
import time


from tqdm import tqdm

# from scipy.interpolate import griddata
from scipy.interpolate import Rbf

from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

import folium
import matplotlib.pyplot as plt
from matplotlib import cm
import matplotlib.dates as mdates
import geojsoncontour

from datetime import datetime

from sklearn.impute import SimpleImputer

import ipywidgets as widgets
from ipywidgets import Layout

import warnings
warnings.filterwarnings('ignore')

In [ ]:
dataset = pd.read_csv("/content/drive/MyDrive/Datasets for ML/File1.csv")

In [ ]:
sensors1 = [[],[],[]]

for i in range(0, dataset.shape[0]):
    list1 = [dataset.iloc[i, 20], dataset.iloc[i, 21], dataset.iloc[i, 22]]
    if sensors1[0].count(list1[0])==0 and sensors1[1].count(list1[1])==0 :
        sensors1[0].append(list1[0])
        sensors1[1].append(list1[1])
        sensors1[2].append(list1[2])


In [ ]:
print(dataset.isnull().sum())

Unnamed: 0                            0
airQualityLevel                       0
observationDateTime                   0
deviceStatus                          0
aqiMajorPollutant                     0
id                                    0
airQualityIndex                       0
uv.avgOverTime                     5321
o3.avgOverTime                     3240
pm2p5.avgOverTime                  6023
co2.avgOverTime                    4840
pm10.avgOverTime                   5959
co.avgOverTime                     3232
no2.avgOverTime                    3214
airTemperature.avgOverTime         6136
illuminance.avgOverTime            6129
ambientNoise.avgOverTime           6081
so2.avgOverTime                    3252
relativeHumidity.avgOverTime       6142
atmosphericPressure.avgOverTime    6069
latitude                              0
longitude                             0
label                                 0
dtype: int64


#Missing Values

In [ ]:
imputer = SimpleImputer(missing_values=np.nan, strategy='mean')
dataset.iloc[:, 6:22] = imputer.fit_transform(dataset.iloc[:, 6:22])

In [ ]:
# print(dataset)

In [ ]:
print(dataset.isnull().sum())

Unnamed: 0                         0
airQualityLevel                    0
observationDateTime                0
deviceStatus                       0
aqiMajorPollutant                  0
id                                 0
airQualityIndex                    0
uv.avgOverTime                     0
o3.avgOverTime                     0
pm2p5.avgOverTime                  0
co2.avgOverTime                    0
pm10.avgOverTime                   0
co.avgOverTime                     0
no2.avgOverTime                    0
airTemperature.avgOverTime         0
illuminance.avgOverTime            0
ambientNoise.avgOverTime           0
so2.avgOverTime                    0
relativeHumidity.avgOverTime       0
atmosphericPressure.avgOverTime    0
latitude                           0
longitude                          0
label                              0
dtype: int64


In [ ]:
for i in range(0, dataset.shape[0]):
    dataset.iloc[i, 2] = dataset.iloc[i , 2][:dataset.iloc[i , 2].find('+')-3]

In [ ]:
# print(dataset)

In [ ]:
column_choice=['airQualityIndex','airTemperature','ambientNoise','so2','uv','co','co2','atmosphericPressure',
               'illuminance','no2','o3','pm10','pm2p5','relativeHumidity']

In [ ]:

prompt1=widgets.HTML(value="")
prompt2=widgets.HTML(value="")
gif_address = 'https://www.uttf.com.ua/assets/images/loader2.gif'

# drop down widget to choose pollutant/property
select_col=widgets.Dropdown(
    options=column_choice,
    value='airQualityIndex',
    description='Property:',
    disabled=False,
)
time_range=[]
for i in range(0, dataset.shape[0]):
    time_range.append(datetime.strptime(dataset.iloc[i , 2], '%Y-%m-%d %H:%M'))
options = [time.strftime('%d %b %H:%M') for time in time_range]
index = (0, len(options)-1)

# Slider to choose time
select_time=widgets.SelectionSlider(
    options=options,
    value=options[25053],
    description='Time:',
    disabled=False,
    orientation='horizontal',
    continuous_update=False,
    readout=True,
    width=6000,
)
mywidgets=[select_col]
ui=widgets.VBox([prompt1,select_col,select_time,prompt2],width=2000)

In [ ]:
# FUNCTION TO PLOT CONTOUR MAP AFTER CUBIC INTERPOLATION
def pollutant_contour(pollutant,time):
    prompt2.value='Building Contour ...'
    
    # GATHER THE REQUIRED DATA FOT THE CHOSEN TIME
    time=datetime.strptime(time+' 2022','%d %b %H:%M %Y')

    # aqm_latest=aqm[aqm.observationDateTime<time.strftime('%d-%m-%Y %H:%M:%S')]
    # aqm_latest=aqm_latest.sort_values(by='observationDateTime').drop_duplicates(['id'],keep='last')
    # print([dataset.observationDateTime<time.strftime('%d-%m-%Y %H:%M:%S'))
    
    time = str(time)
    time = time[:-3]
    
    latest = dataset.loc[dataset['observationDateTime'] == time]
    latest = latest.sort_values(by='observationDateTime').drop_duplicates(['id'],keep='last')

    if(latest.shape == 0):
        print("Missing Values")
    
    else:
        # print(latest)

        if pollutant != 'airQualityIndex':
            pollutant = pollutant+'.avgOverTime'
        
        # data=aqm_latest.dropna(subset=[pollutant])
        data = latest.dropna(subset=[pollutant])
        readings=data[pollutant]
        x=data['longitude']
        y=data['latitude']
        sensors=list(np.unique(data.id))
    
        #BUILDING A MESH GRID FOR A GIVEN RESOLUTION
        res=1000
        y_arr = np.linspace(np.min(y), np.max(y), res)
        x_arr = np.linspace(np.min(x), np.max(x), res)
        x_mesh, y_mesh = np.meshgrid(x_arr, y_arr)
        
        # PERFORM CUBIC INTERPOLATION
        # interpolated_readings = griddata((x, y), readings, (x_mesh, y_mesh), method='cubic')
        print(min(readings))
        print(max(readings))
        rbfi = Rbf(x, y, readings, function='gaussian', mode='1-D', epsilon = 0.012565599999999932)
        interpolated_readings = rbfi(x_mesh, y_mesh)
        
        # PLOT CONTOUR
        levels = 50
        maximum = 0
        minimum = 0
        print(interpolated_readings.shape)
        for abc in interpolated_readings:
            maximum = max(maximum, max(abc)) 
            minimum = min(minimum, min(abc))

        print(maximum)
        print(minimum)
        common_levels = np.linspace(-2744.0, 4086.0, 100)
        # 4085.678369120697 -2743.1165148023774
        
        contourf=plt.contourf(x_mesh, y_mesh, interpolated_readings, levels, alpha=0.5, 
                            cmap=cm.jet, linestyles='None', vmin=0)
        plt.close()

        # CONVERT CONTOUR TO GEOJSON REPRESENTION
        geojson = geojsoncontour.contourf_to_geojson(
            contourf=contourf,
            min_angle_deg=3.0,
            ndigits=5,
            stroke_width=1,
            fill_opacity=0.5)

        sensors_map=folium.Map(tiles="cartodbpositron")
        
        # UNCOMMENT THE FOLLOWING LINES TO PLOT THE SENSOR LOCATIONS AS WELL
        # for rsc_id, rsc in rsc_dict.items():
        #     if rsc_id in sensors:
        #         folium.Marker([rsc["coordinates"][1], rsc["coordinates"][0]],
        #                       tooltip=rsc['label']).add_to(sensors_map)
        
        for i in range(0,len(sensors1[0])):
            folium.Marker(location=[sensors1[0][i], sensors1[1][i]],popup=sensors1[2][i],).add_to(sensors_map)
        # PLOT CONTOUR ON MAP WITH FOLIUM 
        folium.GeoJson(
            geojson,
            style_function=lambda x: {
                'color':     x['properties']['stroke'],
                'weight':    x['properties']['stroke-width'],
                'fillColor': x['properties']['fill'],
                'opacity':   0.6,
            }).add_to(sensors_map)

        sensors_map.fit_bounds(sensors_map.get_bounds())
        
        prompt2.value=str(time)
        
        display(sensors_map)

In [ ]:

display(ui)
widgets.interactive_output(pollutant_contour,{'pollutant':select_col,'time':select_time})
      


Output()

In [ ]:
dataset.loc[dataset["observationDateTime"] == "2022-01-16 19:31"][['airQualityIndex', 'label']]

airQualityIndex                                     label
56702             86.0                  Mundhwa Road Junction_51
56703            165.0                        Chandani Square_25
56704            106.0                     Golf Club Junction_27
56705            183.0                 PMPML_Bus_Depot_Deccan_15
56706             62.0            Shree Krishna Hotel Square _12
56707             97.0                 ABC_Farm_House_Junction_4
56708            225.0                          Bremen Square_37
56709            351.0                   Sinhgad Road Junction_9
56710            193.0                          Nalstop_Square_7
56711            325.0                Ambedkar society circle_29
56712            279.0                     Power_House_Square_43
56713            113.0                  Chitale Bandhu Corner_41
56714            105.0                         Golibar Square_11
56715            217.0                    Jhanshi Rani Square_59
56716            302.0                      Sudhanshu society_36
56717            309.0                          Ptrakar bhavn_72
56718            145.0                   Goodluck Square_Cafe_23
56719            110.0                    Appa_Balwant_Square_30
56720             79.0                     Karve Statue Square_5
56721             57.0                    Datta Mandir Square_66
56722             81.0                      Nanded City Entry_42
56723            124.0                                Susgaon_46
56724            288.0                   Pune Railway Station_28
56725            337.0                Noble Hospital junction_35
56726             89.0                 Kothrud PMPML BusDepot_48
56727             67.0                          Gunjan Square_65
56728             58.0  Dr Baba Saheb Ambedkar Sethu Junction_60
56729            336.0                    BRTS Visharant wadi_38
56730            281.0                      Swargate ST Stand_13
56731            101.0                       Hadapsar_Gadital_01
56732             65.0                   Market Yard Junction_02
56733            153.0                 PMPML Katraj_Depot_New_26
56734            307.0                          Pune_ST_Stand_40
56735            101.0        Blue Diamond Square (Hotel Taj)_10
56736            102.0                          FursungiKaman_31

In [ ]:
sensors1.find('Katraj_Depot_New_26')

AttributeError: ignored

In [ ]:
print((max(dataset.latitude) - min(dataset.latitude))/10)

0.012565599999999932


In [ ]:
print(max(dataset.longitude) - min(dataset.longitude))

0.19878500000000088


In [ ]:
0.125655/10


0.012565499999999999